## Imports

In [ ]:
import sys
!pip install zipcode
!pip install plotly

In [2]:
import pandas as pd
import numpy as np
import folium
import geocoder
import zipcode
import plotly
import plotly.plotly as py
from plotly.graph_objs import *
from folium.plugins import FastMarkerCluster
from folium.plugins import HeatMap
from us_state_abbrev import us_state_abbrev


## Data

In [66]:
df_beers = pd.read_csv('ucsd-sansdescrip03162018.csv', sep="|")
df_beers = df_beers.rename(index=str, columns={'BeerName': 'name', 'BeerStyleName': 'style', 'Entered': 'entry', 'RateCount': 'rate_count', 'BrewerCity': 'city', 'Abbrev':'state', 'BrewerZIPCode':'zipcode'})

df_beers['name'] = df_beers['name'].str.strip()
df_beers['style'] = df_beers['style'].str.strip()
df_beers['city'] = df_beers['city'].str.strip()
df_beers['state'] = df_beers['state'].str.strip()
df_beers['zipcode'] = df_beers['zipcode'].str.strip()


In [67]:
df_beers.head()

name                 style  \
0   Great Adirondack Haystack Blonde Ale  Golden Ale/Blond Ale   
1             Great Divide Bee Sting Ale  Golden Ale/Blond Ale   
2                   Newport Beach Blonde              Pilsener   
3  Newport Beach Poohs Reserve Honey Ale  Golden Ale/Blond Ale   
4        Newport Beach Brewhound Red Ale     American Pale Ale   

                     entry  rate_count           city state zipcode  
0  2003-11-20 08:38:18.000        18.0    Lake Placid    NY   12946  
1  2001-06-26 12:31:04.000       111.0         Denver    CO   80205  
2  2000-05-28 00:30:13.000        24.0  Newport Beach    CA   92663  
3  2000-05-28 00:31:35.000         1.0  Newport Beach    CA   92663  
4  2000-06-01 01:01:56.000         0.0  Newport Beach    CA   92663

### Adding latitude and longitude 

In [68]:
def get_latitude(z):
    try:
        return zipcode.isequal(z).lat
    except:
        return np.nan

def get_longitude(z):
    try:
        return zipcode.isequal(z).lon
    except:
        return np.nan

In [ ]:
# Setting lat/lng columns to beers df
df_beers['lat'] = df_beers.apply(lambda x: get_latitude(x['zipcode']), axis=1)
df_beers['lng'] = df_beers.apply(lambda x: get_longitude(x['zipcode']), axis=1)

In [ ]:
assert len([x for x in df_beers['lng'] if np.isnan(x)]) == len([x for x in df_beers['lat'] if np.isnan(x)])

### Beers by state

In [ ]:
# Counting breweries by state
df_beers_by_state = df_beers.groupby(df_beers['state'].str.strip()).size().reset_index()
df_beers_by_state = df_beers_by_state.rename(index=str, columns={0:'beers_count'})

In [ ]:
df_beers_by_state.head()

In [20]:
assert sum(df_beers_by_state['beers_count']) == (len(df_beers) - 1) # 

### Beers by city

In [21]:
df_beers_by_city = df_beers.groupby([df_beers['state'].str.upper().str.strip(), df_beers['city'].str.capitalize().str.strip()]).size().reset_index()
df_beers_by_city = df_beers_by_city.rename(index=str, columns={0:'beers_count'})

In [22]:
def get_zipcode(city, state):
    try:
        return df_beers['zipcode'][(state == df_beers['state']) & (city == df_beers['city'])][0]
    except:
        return np.nan

In [23]:
# adding zipcode column
df_beers_by_city['zipcode'] = df_beers_by_city.apply(lambda x: get_zipcode(x['city'], x['state']), axis=1)

In [24]:
# Removing NaN
df_beers_by_city = df_beers_by_city[~pd.isnull(df_beers_by_city['zipcode'])]

In [25]:
# Cleaning zip code so that they are of len 5
df_beers_by_city['zipcode'] = df_beers_by_city.apply(lambda x: x['zipcode'][:5], axis=1)

In [26]:
# Setting lat/lng columns to df_beers_by_city
df_beers_by_city['lat'] = df_beers_by_city.apply(lambda x: get_latitude(x['zipcode']), axis=1)
df_beers_by_city['lng'] = df_beers_by_city.apply(lambda x: get_longitude(x['zipcode']), axis=1)

In [27]:
# Removing NaN
df_beers_by_city = df_beers_by_city[~pd.isnull(df_beers_by_city['zipcode'])]

In [28]:
# Sorting data by beers_count
df_beers_by_city = df_beers_by_city.sort_values(by=['beers_count'], ascending=False)

In [29]:
df_beers_by_city.head()

state         city  beers_count zipcode    lat     lng
433     CO       Denver         5414   80205  39.76 -104.87
2613    OR     Portland         5324   97214  45.51 -122.64
889     IL      Chicago         5301   60614    NaN     NaN
3368    WA      Seattle         4760   98105  47.66 -122.29
1631    MN  Minneapolis         3225   55454  44.96  -93.26

### Population Estimates (State)

In [30]:
df_population_estimates = pd.read_csv('raw_data/us_states_population_estimates.csv')
df_population_estimates = df_population_estimates.rename(index=str, columns={'State': 'state', 'Population Estimate': 'population_estimate', 'Year': 'year'})

In [31]:
# Getting latest data (population estimates from 2017), dropping it, and removing Puerto Rico
df_population_estimates = df_population_estimates[df_population_estimates['year'] == 2017]
df_population_estimates = df_population_estimates.drop('year', axis=1)
df_population_estimates = df_population_estimates[df_population_estimates['state'] != 'Puerto Rico']

In [32]:
assert len(df_population_estimates) == 51

In [33]:
# Converting full state name to its abbreviation
df_population_estimates['state'] = df_population_estimates['state'].apply((lambda s: us_state_abbrev[s]))

In [34]:
df_population_estimates.head()

state  population_estimate
364    AL              4874747
365    AK               739795
366    AZ              7016270
367    AR              3004279
368    CA             39536653

### Beers per capita by state

In [35]:
# Merging population estimates and beers by state
df_beers_per_capita = pd.merge(df_population_estimates, df_beers_by_state, on='state')

In [36]:
# Beers per capita (1 beer per 100,000 habitants)
df_beers_per_capita['beers_per_capita'] = df_beers_per_capita.apply((lambda r: int((r['beers_count']/r['population_estimate']) * 100000)), axis=1)

In [37]:
# Dropping beer count and population estimates for Map visualization
df_beers_per_capita = df_beers_per_capita.drop('population_estimate', axis=1)
df_beers_per_capita = df_beers_per_capita.drop('beers_count', axis=1)

In [38]:
df_beers_per_capita.head()

state  beers_per_capita
0    AL                23
1    AK               247
2    AZ                58
3    AR                16
4    CA                92

### Beers by cities

In [57]:
df_beers = df_beers[~np.isnan(df_beers['lat'])]

In [58]:
df_beers_CA = df_beers[df_beers['state'] == 'CA']
df_beers_VT = df_beers[df_beers['state'] == 'VT']

In [59]:
df_beers_CA.head()

name                 style                    entry  \
34          Back Street Blonde  Golden Ale/Blond Ale  2003-03-11 20:40:27.763   
348   North Coast Red Seal Ale     American Pale Ale  2000-05-02 13:39:38.000   
349      North Coast Scrimshaw              Pilsener  2000-10-02 11:01:27.000   
459      North Coast Blue Star             Wheat Ale  2000-10-02 10:59:38.000   
1558    North Coast Black Hart             Dry Stout  2001-05-02 22:03:16.000   

      rate_count         city state zipcode  lat  lng  
34           1.0  Yorba Linda    CA   92686  NaN  NaN  
348       1749.0   Fort Bragg    CA   94357  NaN  NaN  
349       1036.0   Fort Bragg    CA   94357  NaN  NaN  
459        579.0   Fort Bragg    CA   94357  NaN  NaN  
1558       126.0   Fort Bragg    CA   94357  NaN  NaN

In [60]:
df_beers_VT.head()

name                 style  \
94695    Covered Bridge Lucky Me  Golden Ale/Blond Ale   
180154  Covered Bridge Maple Sap             Brown Ale   

                          entry  rate_count         city state zipcode  lat  \
94695   2013-05-08 16:29:48.000         5.0  Lyndonville    VT     NaN  NaN   
180154  2015-10-06 13:11:19.000         0.0  Lyndonville    VT     NaN  NaN   

        lng  
94695   NaN  
180154  NaN

## Maps & Visualization

### Beers by state (Colorpleth)

In [61]:
state_geo = r'data/us-states.json'

beers_state_map = folium.Map(location=[48, -102], zoom_start=3)
beers_state_map.choropleth(
    geo_data=state_geo,
    data=df_beers_by_state,
    threshold_scale=[6000, 12000, 18000, 24000, 30000, 36000],
    key_on='feature.id',
    columns=['state', 'beers_count'],
    fill_color='OrRd', fill_opacity=1, line_opacity=0.1,
    )

In [62]:
beers_state_map

### Beers per capita by state (Colorpleth)

In [63]:
state_geo = r'data/us-states.json'

beers_per_capita_map = folium.Map(location=[48, -102], zoom_start=3)
beers_per_capita_map.choropleth(
    geo_data=state_geo,
    data=df_beers_per_capita,
    threshold_scale=[100, 200, 300, 400, 500, 600],
    key_on='feature.id',
    columns=['state', 'beers_per_capita'],
    fill_color='OrRd', fill_opacity=1, line_opacity=0.1,
    )

In [64]:
beers_per_capita_map

### Beers by city (HeatMap)

In [65]:
data = df_beers_CA.as_matrix(['lat', 'lng']).tolist()
beers_CA_heatmap = folium.Map(location=[36, -120],tiles='stamentoner', zoom_start=5)
HeatMap(data,radius=14).add_to(beers_CA_heatmap)
beers_CA_heatmap

ValueError: data cannot contain NaNs, got:
[[nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, nan], [nan, na

In [47]:
data = df_beers_VT.as_matrix(['lat', 'lng']).tolist()
beers_VT_heatmap = folium.Map(location=[44, -73],tiles='stamentoner', zoom_start=6)
HeatMap(data,radius=15).add_to(beers_VT_heatmap)
beers_VT_heatmap

ValueError: data cannot contain NaNs, got:
[[43.65, -72.32], [43.65, -72.32], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.44, -73.21], [42.86, -72.57], [44.48, -73.22], [42.86, -72.57], [42.86, -72.57], [44.48, -73.22], [44.48, -73.22], [43.65, -72.32], [44.48, -73.22], [44.44, -73.21], [44.48, -73.22], [44.48, -73.22], [43.97, -72.32], [43.97, -72.32], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.44, -73.21], [44.44, -73.21], [44.44, -73.21], [44.44, -73.21], [44.44, -73.21], [44.48, -73.22], [43.28, -72.47], [44.44, -73.21], [44.48, -73.22], [44.44, -73.21], [43.65, -72.32], [44.48, -73.22], [44.48, -73.22], [44.44, -73.21], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.44, -73.21], [44.48, -73.22], [44.48, -73.22], [44.44, -73.21], [44.48, -73.22], [42.86, -72.57], [42.86, -72.57], [42.86, -72.57], [43.28, -72.47], [43.82, -72.52], [44.48, -73.22], [43.28, -72.47], [42.87, -73.18], [44.48, -73.22], [44.

In [48]:
data = df_beers_CA.as_matrix(['lat', 'lng']).tolist() + df_beers_VT.as_matrix(['lat', 'lng']).tolist()
beers_CA_VT_heatmap = folium.Map(location=[40, -102],tiles='stamentoner', zoom_start=4)
HeatMap(data,radius=15).add_to(beers_CA_VT_heatmap)
beers_CA_VT_heatmap

ValueError: data cannot contain NaNs, got:
[[33.62, -117.93], [33.62, -117.93], [33.62, -117.93], [33.62, -117.93], [37.86, -122.25], [37.86, -122.25], [37.86, -122.25], [33.62, -117.93], [32.79, -117.06], [nan, nan], [35.38, -120.78], [38.99, -123.36], [38.13, -122.56], [36.89, -121.24], [35.38, -120.78], [34.14, -118.16], [38.99, -123.36], [37.76, -122.39], [37.74, -122.41], [37.74, -122.41], [34.14, -118.16], [38.99, -123.36], [34.17, -118.17], [38.99, -123.36], [37.74, -122.41], [34.17, -118.17], [37.76, -122.39], [37.76, -122.48], [37.76, -122.39], [37.38, -122.07], [37.38, -122.07], [33.13, -117.3], [37.76, -122.48], [37.86, -122.25], [33.99, -117.44], [38.84, -120.01], [38.84, -120.01], [33.62, -117.93], [37.71, -122.16], [37.86, -122.25], [37.86, -122.25], [34.41, -119.7], [nan, nan], [nan, nan], [33.53, -117.1], [38.62, -121.38], [37.16, -122.15], [34.04, -118.44], [35.25, -120.62], [39.12, -123.28], [37.65, -121.85], [37.65, -121.85], [33.67, -118.0], [32.79, -117.23], [32.79

### Beers by city (MarkerCluster)

In [49]:
data = df_beers_CA.as_matrix(['lat', 'lng']).tolist()
beers_CA_markermap = folium.Map(location=[37, -120], zoom_start=6)
FastMarkerCluster(data=data).add_to(beers_CA_markermap)
beers_CA_markermap

ValueError: Location values cannot contain NaNs, got:
[[33.62, -117.93], [33.62, -117.93], [33.62, -117.93], [33.62, -117.93], [37.86, -122.25], [37.86, -122.25], [37.86, -122.25], [33.62, -117.93], [32.79, -117.06], [nan, nan], [35.38, -120.78], [38.99, -123.36], [38.13, -122.56], [36.89, -121.24], [35.38, -120.78], [34.14, -118.16], [38.99, -123.36], [37.76, -122.39], [37.74, -122.41], [37.74, -122.41], [34.14, -118.16], [38.99, -123.36], [34.17, -118.17], [38.99, -123.36], [37.74, -122.41], [34.17, -118.17], [37.76, -122.39], [37.76, -122.48], [37.76, -122.39], [37.38, -122.07], [37.38, -122.07], [33.13, -117.3], [37.76, -122.48], [37.86, -122.25], [33.99, -117.44], [38.84, -120.01], [38.84, -120.01], [33.62, -117.93], [37.71, -122.16], [37.86, -122.25], [37.86, -122.25], [34.41, -119.7], [nan, nan], [nan, nan], [33.53, -117.1], [38.62, -121.38], [37.16, -122.15], [34.04, -118.44], [35.25, -120.62], [39.12, -123.28], [37.65, -121.85], [37.65, -121.85], [33.67, -118.0], [32.79, -117.

In [50]:
data = df_beers_VT.as_matrix(['lat', 'lng']).tolist()
beers_VT_markermap = folium.Map(location=[44, -73], zoom_start=7)
FastMarkerCluster(data=data).add_to(beers_VT_markermap)
beers_VT_markermap

ValueError: Location values cannot contain NaNs, got:
[[43.65, -72.32], [43.65, -72.32], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.44, -73.21], [42.86, -72.57], [44.48, -73.22], [42.86, -72.57], [42.86, -72.57], [44.48, -73.22], [44.48, -73.22], [43.65, -72.32], [44.48, -73.22], [44.44, -73.21], [44.48, -73.22], [44.48, -73.22], [43.97, -72.32], [43.97, -72.32], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.44, -73.21], [44.44, -73.21], [44.44, -73.21], [44.44, -73.21], [44.44, -73.21], [44.48, -73.22], [43.28, -72.47], [44.44, -73.21], [44.48, -73.22], [44.44, -73.21], [43.65, -72.32], [44.48, -73.22], [44.48, -73.22], [44.44, -73.21], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.48, -73.22], [44.44, -73.21], [44.48, -73.22], [44.48, -73.22], [44.44, -73.21], [44.48, -73.22], [42.86, -72.57], [42.86, -72.57], [42.86, -72.57], [43.28, -72.47], [43.82, -72.52], [44.48, -73.22], [43.28, -72.47], [42.87, -73.18], [44.48, -7

In [51]:
data = df_beers_CA.as_matrix(['lat', 'lng']).tolist() + df_beers_VT.as_matrix(['lat', 'lng']).tolist()
beers_markermap = folium.Map(location=[40, -102], zoom_start=4)
FastMarkerCluster(data=data).add_to(beers_markermap)
beers_markermap

ValueError: Location values cannot contain NaNs, got:
[[33.62, -117.93], [33.62, -117.93], [33.62, -117.93], [33.62, -117.93], [37.86, -122.25], [37.86, -122.25], [37.86, -122.25], [33.62, -117.93], [32.79, -117.06], [nan, nan], [35.38, -120.78], [38.99, -123.36], [38.13, -122.56], [36.89, -121.24], [35.38, -120.78], [34.14, -118.16], [38.99, -123.36], [37.76, -122.39], [37.74, -122.41], [37.74, -122.41], [34.14, -118.16], [38.99, -123.36], [34.17, -118.17], [38.99, -123.36], [37.74, -122.41], [34.17, -118.17], [37.76, -122.39], [37.76, -122.48], [37.76, -122.39], [37.38, -122.07], [37.38, -122.07], [33.13, -117.3], [37.76, -122.48], [37.86, -122.25], [33.99, -117.44], [38.84, -120.01], [38.84, -120.01], [33.62, -117.93], [37.71, -122.16], [37.86, -122.25], [37.86, -122.25], [34.41, -119.7], [nan, nan], [nan, nan], [33.53, -117.1], [38.62, -121.38], [37.16, -122.15], [34.04, -118.44], [35.25, -120.62], [39.12, -123.28], [37.65, -121.85], [37.65, -121.85], [33.67, -118.0], [32.79, -117.

### Beers by city (Plotly Bubble Maps)

In [52]:
API_KEY = 'iqJqlRcPKIHqjD1B0DVQ'
plotly.tools.set_credentials_file(username='semendez', api_key=API_KEY)

In [53]:
# df = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/2014_us_cities.csv')
df_beers_by_city['text'] = df_beers_by_city['city'] + '<br>Beers: ' + (df_beers_by_city['beers_count']).astype(str)
limits = [(0,3),(3,10),(10,20),(20,50),(50,2000)]
colors = ["rgb(0,116,217)","rgb(255,65,54)","rgb(133,20,75)","rgb(255,133,27)","lightgrey"]
cities = []
scale = 5

In [54]:
for i in range(len(limits)):
    lim = limits[i]
    df_sub = df_beers_by_city[lim[0]:lim[1]]
    city = dict(
        type = 'scattergeo',
        locationmode = 'USA-states',
        lon = df_sub['lng'],
        lat = df_sub['lat'],
        text = df_sub['text'],
        marker = dict(
            size = df_sub['beers_count']//scale,
            color = colors[i],
            line = dict(width=0.5, color='rgb(40,40,40)'),
            sizemode = 'area'
        ),
        name = '{0} - {1}'.format(lim[0],lim[1]) )
    cities.append(city)

In [55]:
layout = dict(
        title = '2014 US city populations<br>(Click legend to toggle traces)',
        showlegend = True,
        geo = dict(
            scope='usa',
            projection=dict( type='albers usa' ),
            showland = True,
            landcolor = 'rgb(217, 217, 217)',
            subunitwidth=1,
            countrywidth=1,
            subunitcolor="rgb(255, 255, 255)",
            countrycolor="rgb(255, 255, 255)"
        ),
    )

In [56]:
fig = dict( data=cities, layout=layout )
py.iplot( fig, validate=False, filename='d3-bubble-map-populations', sharing='public')

High five! You successfully sent some data to your account on plotly. View your plot in your browser at https://plot.ly/~semendez/0 or inside your plot.ly account where it is named 'd3-bubble-map-populations'


## Resources

* US States JSON: https://github.com/python-visualization/folium/blob/master/examples/data/us-states.json
* US States Abbreviations: https://gist.githubusercontent.com/rogerallen/1583593/raw/74f2ef57ac82d60dc1e7ae871d1a9c60c9953fac/us_state_abbrev.py
* Population Estimates: https://www.kaggle.com/sheetskg/est-population-us-states-puerto-rico-20102017/data